# Item-based Models

In this file we are going to proceed with the building in the models. Machine learning models to build recommender systems. The models that are going to be built are Collaborative filtering using Item-based rating prediction (ItemKNN) and Item-based classification (ItemKNN).

Collaborative filtering is a technique used in recommendation systems to predict or classify items based on the preferences or behavior of similar users or items. Item-based Collaborative Filtering (CF) focuses on the similarity between items rather than users. There are two main approaches within item-based CF: rating prediction and classification.

In [1]:
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all" # to make jupyter print all outputs, not just the last one
from IPython.core.display import HTML # to pretty print pandas df and be able to copy them over (e.g. to ppt slides)

In [2]:
# We import the necessary libraries
import pandas as pd
import numpy as np
import os

In [3]:
# We print the directory where the file is located
print(os.getcwd())

c:\Users\Jaume\Documents\MDDB\SDM\SDfM---Jaume-and-Stijn 2\SDfM---Jaume-and-Stijn


In [4]:
# We set the directory to the cleaned folder
os.listdir(os.path.join('.', 'cleaned'))

['final_sample30_parquet',
 'final_sample5_parquet',
 'movielens_parquet',
 'netflix_parquet',
 'sample_tenth_netflix',
 'unpacked_reviews_df_100k.parquet']

In [5]:
# We read the final_sample file and store it in a dataframe
df = pd.read_parquet('cleaned/sample_tenth_netflix')

In [6]:
# We print shape of the dataframe
df.shape

(143, 4)

In [7]:
# We print the first 5 rows of the dataframe
df.head()

movieId  year               title  \
123       124  2000        Cold Blooded   
1192    13434  1998          Beast Cops   
462      4601  1994           The Scout   
351       352  1997         Pick a Card   
1057     9560  2000  New World Disorder   

                                            review_data  
123   [{'date': 2002-04-01, 'rating': 3.0, 'userId':...  
1192  [{'date': 2003-02-20, 'rating': 2.0, 'userId':...  
462   [{'date': 2003-12-27, 'rating': 3.0, 'userId':...  
351   [{'date': 2003-10-13, 'rating': 4.0, 'userId':...  
1057  [{'date': 2003-07-06, 'rating': 4.0, 'userId':...

In [8]:
# We print the columns of the dataframe
df.columns

Index(['movieId', 'year', 'title', 'review_data'], dtype='object')

In [10]:
import pandas as pd

# Assuming your DataFrame is named df

# Step 1: Explode the review_data column
exploded_df = df.explode('review_data').reset_index(drop=True)


In [11]:
exploded_df.head()

exploded_df.shape

# We get the first row of exploded_df
exploded_df.iloc[0]

movieId  year         title  \
0      124  2000  Cold Blooded   
1      124  2000  Cold Blooded   
2      124  2000  Cold Blooded   
3      124  2000  Cold Blooded   
4      124  2000  Cold Blooded   

                                         review_data  
0  {'date': 2002-04-01, 'rating': 3.0, 'userId': ...  
1  {'date': 2002-05-14, 'rating': 3.0, 'userId': ...  
2  {'date': 2001-06-06, 'rating': 3.0, 'userId': ...  
3  {'date': 2001-07-28, 'rating': 2.0, 'userId': ...  
4  {'date': 2002-02-04, 'rating': 1.0, 'userId': ...

(798963, 4)

movieId                                                      124
year                                                        2000
title                                               Cold Blooded
review_data    {'date': 2002-04-01, 'rating': 3.0, 'userId': ...
Name: 0, dtype: object

In [12]:

# Step 2: Convert the exploded dictionary column into separate columns
expanded_review_data = pd.json_normalize(exploded_df['review_data'])


In [13]:
expanded_review_data.head()

date  rating   userId
0  2002-04-01     3.0    68845
1  2002-05-14     3.0   349975
2  2001-06-06     3.0  1619594
3  2001-07-28     2.0  2377588
4  2002-02-04     1.0  1361044

In [14]:

# Step 3: Concatenate the expanded data with the original DataFrame
df = pd.concat([exploded_df.drop('review_data', axis=1), expanded_review_data], axis=1)

# Verify the shape of the final DataFrame
print("Final DataFrame shape:", df.shape)


Final DataFrame shape: (798963, 6)


In [15]:
df.head()

movieId  year         title        date  rating   userId
0      124  2000  Cold Blooded  2002-04-01     3.0    68845
1      124  2000  Cold Blooded  2002-05-14     3.0   349975
2      124  2000  Cold Blooded  2001-06-06     3.0  1619594
3      124  2000  Cold Blooded  2001-07-28     2.0  2377588
4      124  2000  Cold Blooded  2002-02-04     1.0  1361044

In [16]:
# We print the number of unique users and movies
print(df['userId'].nunique())
print(df['movieId'].nunique())


254268
134


In [17]:
# Check if there are userIDs that haven't rated movies at all
print(df['userId'].value_counts().sort_values(ascending=False))

# Check if there are movieIDs that haven't been rated at all
print(df['movieId'].value_counts().sort_values(ascending=False))

userId
305344     133
387418     132
2439493    127
1664010    122
2118461    121
          ... 
1924932      1
2609901      1
850692       1
1040716      1
773753       1
Name: count, Length: 254268, dtype: int64
movieId
30      118413
4705     58536
290      47651
4727     41128
199      35509
         ...  
193        121
352        119
9385       117
219        111
4571       104
Name: count, Length: 134, dtype: int64


In [18]:
# Get the rating for movieID 4966
df[df['movieId'] == 4966]

Empty DataFrame
Columns: [movieId, year, title, date, rating, userId]
Index: []

In [19]:
# Check if there are NaN values in the rating column
df['rating'].isna().sum()

0

In [20]:
# We take a sample of 5% of the data
df = df.sample(frac=0.05, random_state=42)

# Item-based Rating Prediction (ItemKNN)

### Step 1: User-Item matrix construction
The first thing we have to do is build the user-item matrix:

- Choose a similarity metric to calculate the similarity between items. Common metrics include cosine similarity, Pearson correlation coefficient, and Jaccard similarity.
- Calculate the similarity between each pair of items based on the ratings provided by users. This will result in an item-item similarity matrix.

#### Collaborative Filtering with Cosine Similarity

This code snippet demonstrates how to perform item-based collaborative filtering using cosine similarity. Collaborative filtering is a technique commonly used in recommendation systems to predict a user's preferences for items based on the preferences of similar users/items.

##### Libraries Used
- **pandas**: A powerful data manipulation library in Python.
- **numpy**: A library for numerical computing in Python.
- **sklearn.metrics.pairwise.cosine_similarity**: A function from scikit-learn used to compute the cosine similarity between vectors.

In [21]:
import pandas as pd
import numpy as np

# Assuming df is your DataFrame with the specified format
# Convert userId column to integer type if needed
if df['userId'].dtype != int:
    df['userId'] = df['userId'].astype(int)

# Get all unique user IDs and movie IDs
all_user_ids = np.unique(df['userId'])
all_movie_ids = np.unique(df['movieId'])

# Create a DataFrame with all combinations of user IDs and movie IDs
all_user_movie_pairs = np.array(np.meshgrid(all_user_ids, all_movie_ids)).T.reshape(-1, 2)
df_pairs = pd.DataFrame(all_user_movie_pairs, columns=['userId', 'movieId'])

# Merge the original DataFrame with all_user_movie_pairs to fill missing ratings with 0
df_filled = pd.merge(df_pairs, df, on=['userId', 'movieId'], how='left').fillna(0)

# Create user-item matrix using pivot_table
item_user_matrix = pd.pivot_table(df_filled, values='rating', index='userId', columns='movieId', fill_value=0)

# Convert user-item matrix to NumPy array for faster computation
item_user_array = item_user_matrix.to_numpy()


In [22]:
item_user_matrix.head()

movieId  30     33     44     45     50     52     66     68     71     77     \
userId                                                                          
79         0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
168        4.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
330        0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
333        0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
379        0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

movieId  ...  13576  13581  13594  13596  13625  13626  13629  13656  13668  \
userId   ...                                                                  
79       ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
168      ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
330      ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
333      ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
379      ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

movieId  13673  
userId          
79         0.0  
168        0.0  
330        0.0  
333        0.0  
379        0.0  

[5 rows x 134 columns]

In [23]:
item_user_array

array([[0., 0., 0., ..., 0., 0., 0.],
       [4., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [4., 0., 0., ..., 0., 0., 0.],
       [5., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

### Train-test split

The train-val-test split is a technique used in machine learning to evaluate the performance of a model. It involves dividing the dataset into three subsets: the training set, the validation set, and the test set.

The training set is used to train the model and optimize its parameters.
The validation set is used to fine-tune the model and select the best hyperparameters.
The test set is used to evaluate the final performance of the model on unseen data.
By using a train-val-test split, we can assess the model's performance on unseen data and ensure that it generalizes well to new examples. It helps prevent overfitting and provides a more reliable estimate of the model's performance in real-world scenarios.

In [24]:
from sklearn.model_selection import train_test_split
# Split the data into training and test sets
train_val, test = train_test_split(item_user_array, test_size=0.2, random_state=42)

# Split the training set into training and validation sets
train, val = train_test_split(train_val, test_size=0.2, random_state=42)

# Print the shapes of the datasets
print("Training set shape:", train.shape)
print("Validation set shape:", val.shape)
print("Test set shape:", test.shape)

# We are also going to do the split for the matrix df
# Split the user-item matrix into training and test sets
train_val_matrix, test_matrix = train_test_split(item_user_matrix, test_size=0.2, random_state=42)

# Split the training set matrix into training and validation sets
train_matrix, val_matrix = train_test_split(train_val_matrix, test_size=0.2, random_state=42)

# We print a ' ' to give some space inbetween lines
print(' ')

# Print the shapes of the matrix datasets
print("Training set matrix shape:", train_matrix.shape)
print("Validation set matrix shape:", val_matrix.shape)
print("Test set matrix shape:", test_matrix.shape)


Training set shape: (22544, 134)
Validation set shape: (5636, 134)
Test set shape: (7045, 134)
 
Training set matrix shape: (22544, 134)
Validation set matrix shape: (5636, 134)
Test set matrix shape: (7045, 134)


In [25]:
train_matrix

movieId  30     33     44     45     50     52     66     68     71     77     \
userId                                                                          
673918     0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1787640    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1442331    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1802986    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
61027      0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
...        ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
553087     0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
924922     0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
558005     0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1886312    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1795561    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

movieId  ...  13576  13581  13594  13596  13625  13626  13629  13656  13668  \
userId   ...                                                                  
673918   ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1787640  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1442331  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1802986  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
61027    ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
553087   ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
924922   ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
558005   ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1886312  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1795561  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

movieId  13673  
userId          
673918     0.0  
1787640    5.0  
1442331    0.0  
1802986    0.0  
61027      0.0  
...        ...  
553087     0.0  
924922     0.0  
558005     0.0  
1886312    0.0  
1795561    0.0  

[22544 rows x 134 columns]

In [26]:
train

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 5.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [27]:
# Calculate cosine similarity between items using NumPy functions
def cosine_similarity(a, b):
    dot_product = np.dot(a, b)
    norm_a = np.linalg.norm(a)
    norm_b = np.linalg.norm(b)
    similarity = dot_product / (norm_a * norm_b)
    return similarity

# Calculate item-item similarity matrix for train data
item_similarity_matrix_train = np.zeros((train.shape[1], train.shape[1]))

for i in range(train.shape[1]):
    for j in range(i, train.shape[1]):
        item_similarity_matrix_train[i, j] = cosine_similarity(train[:, i], train[:, j])
        item_similarity_matrix_train[j, i] = item_similarity_matrix_train[i, j]

# Adjusting the mapping to start indexing from 0
user_id_to_index = {user_id: i for i, user_id in enumerate(item_user_matrix.index)}
index_to_user_id = {i: user_id for i, user_id in enumerate(item_user_matrix.index)}

# Create a mapping from movie IDs to indices
movie_id_to_index = {movie_id: i for i, movie_id in enumerate(item_user_matrix.columns)}
index_to_movie_id = {i: movie_id for i, movie_id in enumerate(item_user_matrix.columns)}


KeyboardInterrupt: 

In [ ]:
movie_id_to_index

{59: 0,
 199: 1,
 201: 2,
 437: 3,
 466: 4,
 478: 5,
 492: 6,
 527: 7,
 561: 8,
 592: 9,
 602: 10,
 609: 11,
 684: 12,
 695: 13,
 769: 14,
 788: 15,
 939: 16,
 967: 17,
 1069: 18,
 1070: 19,
 1276: 20,
 1310: 21,
 1315: 22,
 1333: 23,
 1353: 24,
 1507: 25,
 1573: 26,
 1590: 27,
 1689: 28,
 1701: 29,
 1715: 30,
 1830: 31,
 2128: 32,
 2133: 33,
 2213: 34,
 2225: 35,
 2280: 36,
 2385: 37,
 2693: 38,
 2757: 39,
 2794: 40,
 2807: 41,
 2892: 42,
 2900: 43,
 2960: 44,
 2976: 45,
 3069: 46,
 3184: 47,
 3406: 48,
 3458: 49,
 3595: 50,
 3798: 51,
 3984: 52,
 4011: 53,
 4127: 54,
 4277: 55,
 4306: 56,
 4477: 57,
 4504: 58,
 4580: 59,
 4700: 60,
 4905: 61,
 4906: 62,
 5356: 63,
 5399: 64,
 5446: 65,
 5575: 66,
 5646: 67,
 5652: 68,
 5710: 69,
 5741: 70,
 5775: 71,
 5823: 72,
 5951: 73,
 5980: 74,
 6013: 75,
 6062: 76,
 6082: 77,
 6130: 78,
 6172: 79,
 6173: 80,
 6265: 81,
 6373: 82,
 6402: 83,
 6408: 84,
 6416: 85,
 6460: 86,
 6504: 87,
 6529: 88,
 6544: 89,
 6694: 90,
 6766: 91,
 6785: 92,
 6815:

In [ ]:
print(index_to_user_id)

{0: 30, 1: 33, 2: 44, 3: 45, 4: 50, 5: 52, 6: 66, 7: 68, 8: 71, 9: 77, 10: 79, 11: 102, 12: 116, 13: 124, 14: 164, 15: 169, 16: 185, 17: 193, 18: 199, 19: 209, 20: 219, 21: 221, 22: 232, 23: 234, 24: 238, 25: 240, 26: 248, 27: 271, 28: 278, 29: 290, 30: 298, 31: 310, 32: 311, 33: 333, 34: 340, 35: 345, 36: 352, 37: 354, 38: 355, 39: 359, 40: 4506, 41: 4509, 42: 4513, 43: 4521, 44: 4554, 45: 4571, 46: 4578, 47: 4592, 48: 4600, 49: 4601, 50: 4610, 51: 4625, 52: 4636, 53: 4666, 54: 4667, 55: 4671, 56: 4693, 57: 4705, 58: 4727, 59: 4729, 60: 4730, 61: 4733, 62: 4738, 63: 4744, 64: 4746, 65: 4752, 66: 4758, 67: 4761, 68: 4768, 69: 4777, 70: 4788, 71: 4790, 72: 4805, 73: 9214, 74: 9218, 75: 9233, 76: 9240, 77: 9249, 78: 9255, 79: 9270, 80: 9305, 81: 9311, 82: 9317, 83: 9319, 84: 9329, 85: 9331, 86: 9339, 87: 9348, 88: 9367, 89: 9368, 90: 9372, 91: 9385, 92: 9389, 93: 9390, 94: 9403, 95: 9412, 96: 9436, 97: 9441, 98: 9467, 99: 9469, 100: 9496, 101: 9508, 102: 9521, 103: 9534, 104: 9550, 105: 

In [ ]:
print(user_id_to_index)

{30: 0, 33: 1, 44: 2, 45: 3, 50: 4, 52: 5, 66: 6, 68: 7, 71: 8, 77: 9, 79: 10, 102: 11, 116: 12, 124: 13, 164: 14, 169: 15, 185: 16, 193: 17, 199: 18, 209: 19, 219: 20, 221: 21, 232: 22, 234: 23, 238: 24, 240: 25, 248: 26, 271: 27, 278: 28, 290: 29, 298: 30, 310: 31, 311: 32, 333: 33, 340: 34, 345: 35, 352: 36, 354: 37, 355: 38, 359: 39, 4506: 40, 4509: 41, 4513: 42, 4521: 43, 4554: 44, 4571: 45, 4578: 46, 4592: 47, 4600: 48, 4601: 49, 4610: 50, 4625: 51, 4636: 52, 4666: 53, 4667: 54, 4671: 55, 4693: 56, 4705: 57, 4727: 58, 4729: 59, 4730: 60, 4733: 61, 4738: 62, 4744: 63, 4746: 64, 4752: 65, 4758: 66, 4761: 67, 4768: 68, 4777: 69, 4788: 70, 4790: 71, 4805: 72, 9214: 73, 9218: 74, 9233: 75, 9240: 76, 9249: 77, 9255: 78, 9270: 79, 9305: 80, 9311: 81, 9317: 82, 9319: 83, 9329: 84, 9331: 85, 9339: 86, 9348: 87, 9367: 88, 9368: 89, 9372: 90, 9385: 91, 9389: 92, 9390: 93, 9403: 94, 9412: 95, 9436: 96, 9441: 97, 9467: 98, 9469: 99, 9496: 100, 9508: 101, 9521: 102, 9534: 103, 9550: 104, 9552:

In [ ]:
item_user_array.shape

(35091, 143)

In [ ]:
item_user_matrix.shape

(35091, 143)

In [ ]:
# We print the item_similarity_matrix
item_similarity_matrix_train

array([[1.        , 0.00526447, 0.00662313, ..., 0.00357708, 0.        ,
        0.01711983],
       [0.00526447, 1.        , 0.        , ..., 0.00236329, 0.        ,
        0.00572515],
       [0.00662313, 0.        , 1.        , ..., 0.        , 0.        ,
        0.00608108],
       ...,
       [0.00357708, 0.00236329, 0.        , ..., 1.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 1.        ,
        0.        ],
       [0.01711983, 0.00572515, 0.00608108, ..., 0.        , 0.        ,
        1.        ]])

In [ ]:
item_similarity_matrix_train.shape

(143, 143)

### Step 2: Neighborhood Selection
- Determine the neighborhood size, i.e., the number of most similar items to consider when predicting ratings for a target item.
- Select the most similar items for each item in your dataset based on their calculated similarities. This forms the neighborhood for each item.

#### Item-Based Neighborhoods and Ratings Aggregation

This code following snippet enhances the previous item-based collaborative filtering approach by considering ratings aggregation within the item neighborhoods.

##### Steps:

1. **Defining Neighborhood Size**:
   - The variable `neighborhood_size` determines the number of most similar items to consider in the neighborhood.

2. **Initializing Data Structure**:
   - An empty dictionary `item_neighborhoods` is initialized to store the neighborhoods for each item.

3. **Iterating Over Items**:
   - For each movie in the dataset:
     - All ratings for the current movie are extracted from the DataFrame (`df`).
     - Ratings aggregation is performed. In this example, the average rating for the movie is computed, but other aggregation methods can be used.
     - The similarity scores for the current movie are retrieved from the precomputed `item_similarity_matrix`.
     - Similarity scores are sorted in descending order, and the indices of the most similar items (excluding itself) are obtained.
     - These indices are converted back to movie IDs, forming the neighborhood for the current item.
     - The neighborhood for the current item is stored in the `item_neighborhoods` dictionary.

4. **Output**:
   - `item_neighborhoods`: A dictionary where keys are movie IDs, and values are lists of movie IDs representing the neighborhood of each item. Each movie's neighborhood includes movies with similar ratings and content.

##### Note:
- This approach considers both similarity in ratings and content (as captured by cosine similarity) when building item neighborhoods.
- Aggregating ratings within item neighborhoods helps in providing more personalized recommendations.
- The choice of rating aggregation method (e.g., mean, median) can impact the quality of recommendations and may need to be adjusted based on the characteristics of the dataset and user preferences.


In [ ]:
# Step 2: Neighborhood Selection

# Define the neighborhood size
neighborhood_size = 5

# Initialize an empty dictionary to store item neighborhoods
item_neighborhoods = {}

# Iterate over each item (movie) index in the dataset
for movie_index in range(item_user_array.shape[1]):
    # Convert the item index to movie ID
    movie_id = index_to_movie_id[movie_index]
    
    # Extract all ratings for the current movie
    movie_ratings = item_user_array[:, movie_index]  # Changed to item_user_array
    
    # Aggregate ratings (e.g., compute the mean rating)
    movie_avg_rating = np.mean(movie_ratings)
    
    # Retrieve similarity scores for the current movie
    similarity_scores = item_similarity_matrix_train[movie_index]
    
    # Sort similarity scores in descending order and get indices of most similar items
    most_similar_indices = np.argsort(similarity_scores)[::-1][1:neighborhood_size+1]
    
    # Convert indices back to movie IDs to form the neighborhood
    neighborhood = [index_to_movie_id[idx] for idx in most_similar_indices]
    
    # Store the neighborhood for the current item in the item_neighborhoods dictionary
    item_neighborhoods[movie_id] = neighborhood

# Output: item_neighborhoods dictionary containing neighborhoods for each item
print(item_neighborhoods)


{59: [59, 10268, 7601, 4477, 9891], 199: [199, 9582, 6544, 9133, 527], 201: [201, 7394, 6408, 3458, 3984], 437: [437, 10032, 6013, 1315, 2794], 466: [466, 492, 8200, 4906, 6416], 478: [478, 1069, 7580, 684, 10032], 492: [492, 466, 6416, 4477, 2976], 527: [527, 2133, 7620, 199, 2807], 561: [561, 9928, 2128, 1573, 1507], 592: [592, 8945, 4477, 8207, 7620], 602: [602, 1276, 5446, 7599, 10032], 609: [609, 4504, 59, 3069, 3595], 684: [684, 2385, 1830, 2757, 7580], 695: [695, 10268, 3984, 3595, 3458], 769: [769, 7580, 5646, 6408, 10121], 788: [788, 8092, 6062, 9582, 2794], 939: [939, 8965, 7599, 9850, 6529], 967: [967, 2280, 3798, 3595, 3458], 1069: [1069, 4504, 1689, 6544, 478], 1070: [1070, 1715, 9582, 6504, 2225], 1276: [1276, 602, 10268, 3069, 3595], 1310: [1310, 59, 2280, 3595, 3458], 1315: [1315, 6529, 4477, 8754, 6785], 1333: [1333, 10268, 2280, 3595, 3458], 1353: [1353, 5710, 5980, 4504, 2757], 1507: [1507, 4580, 2225, 6062, 2757], 1573: [1573, 7921, 561, 10016, 5980], 1590: [1590, 2

### Step 4: Rating Prediction

- For each target item and user pair where the user hasn't rated the target item:
Identify the neighborhood of similar items to the target item.
- Predict the rating for the target item using a weighted average of the ratings of the items in its neighborhood, where the weights are the similarities between the items and the target item.
- Adjust the prediction based on the user's average rating or other normalization techniques, if necessary.

In [ ]:
# Train your model and create the item_neighborhoods dictionary using the training data (steps 1-3)

# Initialize an empty DataFrame to store predicted ratings
predicted_ratings = pd.DataFrame(index=train_matrix.index, columns=train_matrix.columns)

# Iterate over each user-item pair in the training set
for user_id, user_ratings in train_matrix.iterrows():
    for movie_id, rating in user_ratings.items():
        
        # Skip if the rating is non-zero (indicating a rating given by the user)
        if rating != 0:
            continue
        
        # Check if the movie has a neighborhood defined
        if movie_id in item_neighborhoods:
            neighborhood = item_neighborhoods[movie_id]
            
            # Filter out movies from the neighborhood that the user has rated in the training set
            filtered_neighborhood = [neighbor_movie_id for neighbor_movie_id in neighborhood if neighbor_movie_id in user_ratings.index and user_ratings.loc[neighbor_movie_id] != 0]
            
            # Check if there are valid indices in the filtered neighborhood
            if len(filtered_neighborhood) > 0:
                # Calculate the predicted rating for the target movie based on the neighborhood
                neighbor_ratings = [user_ratings.loc[neighbor_movie_id] for neighbor_movie_id in filtered_neighborhood]
                
                # Calculate the mean rating using only the movies in the neighborhood that have been rated by the user
                predicted_rating = np.mean(neighbor_ratings)
            else:
                # If the filtered neighborhood is empty, assign the mean rating of all movies rated by the user
                predicted_rating = user_ratings[user_ratings != 0].mean()
            
            # Assign the predicted rating to the corresponding cell in the DataFrame
            predicted_ratings.at[user_id, movie_id] = predicted_rating

# Fill NaN values with mean ratings across all users
predicted_ratings.fillna(predicted_ratings.mean().mean(), inplace=True)

# Display the head of the predicted_ratings DataFrame
predicted_ratings.head()


C:\Users\Jaume\AppData\Local\Temp\ipykernel_1720\1604543681.py:36: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  predicted_ratings.fillna(predicted_ratings.mean().mean(), inplace=True)


movieId     30        33        44        45        50        52        66     \
userId                                                                          
704856   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
910768   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
1463003  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
147790   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
42104    3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   

movieId     68        71        77     ...     13576     13581     13594  \
userId                                 ...                                 
704856   3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
910768   3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
1463003  3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
147790   3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
42104    3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   

movieId     13596     13625     13626     13629     13656     13668     13673  
userId                                                                         
704856   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  
910768   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  
1463003  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  
147790   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  
42104    3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  

[5 rows x 143 columns]

In [ ]:
# We count the NaN values in the predicted_ratings dataframe
predicted_ratings.isnull().sum().sum()

0

In [ ]:
def get_top_recommendations(user_id, predicted_ratings, df):
    """
    Get top movie recommendations for a given user using predicted ratings.

    Parameters:
        user_id (int): ID of the user for whom recommendations are to be generated.
        predicted_ratings (pd.DataFrame): DataFrame containing predicted ratings for users and movies.
        df (pd.DataFrame): DataFrame containing movie ratings.

    Returns:
        list: Top movie titles recommended for the user.
    """
    # Ensure that predicted_ratings is a DataFrame
    if not isinstance(predicted_ratings, pd.DataFrame):
        raise ValueError("predicted_ratings must be a pandas DataFrame")

    # Check if the user ID exists in the predicted ratings DataFrame's index
    if user_id not in predicted_ratings.index:
        # If the user ID doesn't exist, return an empty list
        return ["The user doesn't exist"]

    # Get the predicted ratings for the user
    user_predicted_ratings = predicted_ratings.loc[user_id]
    
    # Filter out the movies that the user has already seen
    seen_movies = set(df[df['userId'] == user_id]['movieId'])
    unseen_movies = [movie_id for movie_id in user_predicted_ratings.index if movie_id not in seen_movies]
    
    # Check if there are unseen movies with predicted ratings
    if not unseen_movies:
        # If all movies have been seen, return an empty list
        return []
    
    # Sort the unseen movies by predicted rating in descending order
    sorted_unseen_movies = user_predicted_ratings[unseen_movies].sort_values(ascending=False)
    
    # Get the top 5 movie titles
    top_movie_ids = sorted_unseen_movies.head(5).index.tolist()
    
    # Get the unique movie titles corresponding to the top movie IDs
    top_movie_titles = set(df[df['movieId'].isin(top_movie_ids)]['title'])
    
    return list(top_movie_titles)[:5]  # Return only the first 5 unique movie titles


In [ ]:
top_recommendations = []

# Iterate over each row (user) in the train_matrix
for user_id in train_matrix.index:
    # Get the actual user ID corresponding to the user index
    recommendations = get_top_recommendations(user_id, predicted_ratings, df)
    top_recommendations.append(recommendations)

# Output: List of top movie recommendations for each user in the train matrix
top_recommendations

# print size of top_recommendations
len(top_recommendations)


[['Mars Needs Women',
  'Bikini Bandits: Briefs, Shorts & Panties',
  "Something's Gotta Give",
  'Benedict Arnold: A Question of Honor',
  'Striptease'],
 ['Aqua Teen Hunger Force: Vol. 1',
  'Mars Needs Women',
  'Bikini Bandits: Briefs, Shorts & Panties',
  'Benedict Arnold: A Question of Honor',
  'Striptease'],
 ['Legend of Crystania: The Chaos Ring',
  'Bikini Bandits: Briefs, Shorts & Panties',
  'Benedict Arnold: A Question of Honor',
  'Striptease',
  'The Deer Hunter'],
 ['Mars Needs Women',
  'Bikini Bandits: Briefs, Shorts & Panties',
  "Something's Gotta Give",
  'Benedict Arnold: A Question of Honor',
  'Striptease'],
 ['Mars Needs Women',
  'Bikini Bandits: Briefs, Shorts & Panties',
  "Something's Gotta Give",
  'Benedict Arnold: A Question of Honor',
  'Striptease'],
 ['Legend of Crystania: The Chaos Ring',
  'Bikini Bandits: Briefs, Shorts & Panties',
  'Benedict Arnold: A Question of Honor',
  'Striptease',
  'The Deer Hunter'],
 ['Legend of Crystania: The Chaos Ring

22457

In [ ]:
print("Last version")

Last version


### Step 5: Model Evaluation
- We evaluate the performance of your ItemKNN algorithm using appropriate evaluation metrics such as Root Mean Squared Error (RMSE), Mean Absolute Error (MAE), or others.
- Split your dataset into training and testing sets to assess the model's predictive accuracy on unseen data.

In [ ]:
train.shape

predicted_ratings.shape

(22457, 143)

(22457, 143)

In [ ]:
import numpy as np
from sklearn.metrics import mean_absolute_error, mean_squared_error

def evaluate_model(train_matrix, predicted_ratings):
    """
    Evaluate the model's performance on the training data.

    Parameters:
        train_matrix (numpy.ndarray): Item-user matrix from the training data.
        predicted_ratings (pandas.DataFrame or numpy.ndarray): Predicted ratings DataFrame or array for the training data.

    Returns:
        float: Mean Absolute Error (MAE) on the training data.
        float: Root Mean Squared Error (RMSE) on the training data.
    """
    # Convert predicted_ratings to a numpy array if it's a DataFrame
    if isinstance(predicted_ratings, pd.DataFrame):
        predicted_ratings = predicted_ratings.to_numpy()

    # Ensure train_matrix and predicted_ratings have the same shape
    assert train_matrix.shape == predicted_ratings.shape, "Shapes of train_matrix and predicted_ratings are not consistent."

    # Initialize lists to store true and predicted ratings
    true_ratings = []
    pred_ratings = []

    # Iterate over each user and their ratings
    for user_id, user_ratings in enumerate(train_matrix):
        for movie_id, rating in enumerate(user_ratings):
            # Skip unrated movies
            if rating == 0:
                continue

            # Check if the indices are within the bounds of the predicted ratings array
            if user_id < predicted_ratings.shape[0] and movie_id < predicted_ratings.shape[1]:
                # Get the predicted rating for the corresponding movie
                pred_rating = predicted_ratings[user_id, movie_id]

                # Append the true and predicted ratings
                true_ratings.append(rating)
                pred_ratings.append(pred_rating)

    # Convert lists to numpy arrays
    true_ratings = np.array(true_ratings)
    pred_ratings = np.array(pred_ratings)

    # Calculate evaluation metrics
    mae = mean_absolute_error(true_ratings, pred_ratings)
    rmse = np.sqrt(mean_squared_error(true_ratings, pred_ratings))

    return mae, rmse

# Assuming train is the numpy array representing the item-user matrix
# Assuming predicted_ratings is the DataFrame or numpy array representing the predicted ratings for the training data

# Evaluate the model
mae, rmse = evaluate_model(train, predicted_ratings)

print("Mean Absolute Error (MAE) on Training Data:", mae)
print("Root Mean Squared Error (RMSE) on Training Data:", rmse)


Mean Absolute Error (MAE) on Training Data: 0.8992261735409154
Root Mean Squared Error (RMSE) on Training Data: 1.0742777997785176


### Step 6: Parameter Tuning
- Experiment with different parameters such as similarity threshold, neighborhood size, and similarity metric to optimize the performance of your ItemKNN algorithm.
- Use cross-validation or other techniques to tune these parameters and avoid overfitting.

1. **Import Necessary Libraries:**
   - We import the required libraries for performing grid search cross-validation (`GridSearchCV`), creating custom scorers (`make_scorer`), and utilizing the `NearestNeighbors` algorithm.

2. **Define Cosine Similarity Function:**
   - We define a custom function `cosine_similarity` to compute the cosine similarity between two vectors. This function calculates the dot product of the vectors and divides it by the product of their norms.

3. **Define Custom Scorer:**
   - We create a custom scorer `cosine_similarity_scorer` using `make_scorer`, which enables us to use cosine similarity as the scoring metric during grid search cross-validation.

4. **Define Parameter Grid:**
   - We specify a parameter grid `param_grid` containing the hyperparameters to be tuned. In this case, we're tuning the number of neighbors (`n_neighbors`) and the distance metric (`metric`) for the `NearestNeighbors` algorithm.

5. **Initialize NearestNeighbors Model:**
   - We initialize the `NearestNeighbors` model without specifying any hyperparameters.

6. **Create GridSearchCV Object:**
   - We create a `GridSearchCV` object named `grid_search` with the specified parameter grid, cross-validation strategy (5-fold cross-validation), and custom scoring metric (`cosine_similarity_scorer`).

7. **Fit the Data:**
   - We fit the `item_user_matrix` data to the `grid_search` object to perform hyperparameter tuning. `item_user_matrix` typically contains the item-item similarity matrix computed using collaborative filtering techniques.

8. **Get Best Hyperparameters:**
   - After fitting the data, we retrieve the best hyperparameters selected by the grid search using the `best_params_` attribute of the `grid_search` object.

9. **Print Best Parameters:**
   - Finally, we print the best hyperparameters obtained from the grid search.



`scikit-learn (sklearn)`:

- Scikit-learn is a popular machine learning library in Python that provides simple and efficient tools for data analysis and modeling.
- It includes various modules for tasks such as classification, regression, clustering, dimensionality reduction, and model selection.
- The GridSearchCV class from scikit-learn is used for hyperparameter tuning through grid search along with cross-validation.
- The make_scorer function allows you to create a custom scoring function for use with GridSearchCV.
- The NearestNeighbors class provides functionality for unsupervised nearest neighbors learning, which can be used for tasks such as finding k-nearest neighbors for a given data point.

In [ ]:
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import NearestNeighbors
from sklearn.metrics import make_scorer
import numpy as np

# Define a custom scorer based on cosine similarity defined above
cosine_similarity_scorer = make_scorer(cosine_similarity)

# Define the parameter grid
param_grid = {
    'n_neighbors': [5, 10, 15, 30, 40],
    'metric': ['cosine', 'euclidean']
}

# Initialize NearestNeighbors model
knn_model = NearestNeighbors()

# Create the GridSearchCV object
grid_search = GridSearchCV(knn_model, param_grid, cv=5, scoring=cosine_similarity_scorer)

# Fit the data to perform hyperparameter tuning
grid_search.fit(train_val_matrix)  # train_val_matrix contains item-user matrix

# Get the best hyperparameters
best_params = grid_search.best_params_

print("Best parameters:", best_params)


c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py:993: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py", line 980, in _score
    scores = scorer(estimator, X_test, **score_params)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
TypeError: _BaseScorer.__call__() missing 1 required positional argument: 'y_true'

  warnings.warn(
c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py:993: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py", line 980, in _score
    scores = scorer(estimator, X_test, **score_

GridSearchCV(cv=5, estimator=NearestNeighbors(),
             param_grid={'metric': ['cosine', 'euclidean'],
                         'n_neighbors': [5, 10, 15, 30, 40]},
             scoring=make_scorer(cosine_similarity, response_method='predict'))

Best parameters: {'metric': 'cosine', 'n_neighbors': 5}


This code sets up a GridSearchCV object to perform hyperparameter tuning using the validation set (train_val_matrix). It explores different combinations of hyperparameters specified in the param_grid, evaluates them using 5-fold cross-validation (cv=5), and uses the cosine_similarity scorer to optimize the model's performance based on cosine similarity. Finally, it prints the best hyperparameters found during the search.

We have to perform the calculation of the predicted ratings for the train-val set to generate predicted ratings in order to evaluate the performance of our trained model on a validation dataset. 

If we computed the similarity matrix again specifically for the train_val set, it would essentially mean that we are using a different set of similarity measures for predicting ratings compared to what we used during training. This approach could lead to inconsistencies and potentially degrade the performance of our model. Here's what could happen:

1. **Inconsistency**: The similarity measures computed for the train_val set might differ from those computed for the training set due to variations in the data. As a result, the predicted ratings based on these new similarity measures may not align well with the predictions made during training, leading to inconsistency in the model's behavior.

2. **Overfitting**: Computing a new similarity matrix specifically for the train_val set might lead to overfitting on the validation data. The model may capture noise or idiosyncrasies present in the train_val set, which may not generalize well to unseen data.

3. **Increased Complexity**: Computing the similarity matrix again for the train_val set adds computational complexity and redundancy, especially if the similarity computation process is resource-intensive. This can result in longer training times and increased resource utilization.

Overall, it's generally recommended to use the same similarity measures or neighborhood definitions for both training and validation sets to ensure consistency and generalizability of the model.

In [ ]:
# Assuming you have already trained your model and obtained the item_neighborhoods dictionary

# Initialize an empty DataFrame to store predicted ratings for train_val
predicted_ratings_train_val = pd.DataFrame(index=train_val_matrix.index, columns=train_val_matrix.columns)

# Iterate over each user and their ratings in the train_val set
for user_id, user_ratings in train_val_matrix.iterrows():
    for movie_id, rating in user_ratings.items():
        # Skip if the rating is non-zero (indicating a rating given by the user)
        if rating != 0:
            continue
        
        # Check if the movie has a neighborhood defined
        if movie_id in item_neighborhoods:
            neighborhood = item_neighborhoods[movie_id]
            
            # Filter out movies from the neighborhood that the user has rated in the train set
            filtered_neighborhood = [neighbor_movie_id for neighbor_movie_id in neighborhood if neighbor_movie_id in user_ratings.index and user_ratings.loc[neighbor_movie_id] != 0]
            
            # Check if there are valid indices in the filtered neighborhood
            if len(filtered_neighborhood) > 0:
                # Calculate the predicted rating for the target movie based on the neighborhood
                neighbor_ratings = [user_ratings.loc[neighbor_movie_id] for neighbor_movie_id in filtered_neighborhood]
                
                # Calculate the mean rating using only the movies in the neighborhood that have been rated by the user
                predicted_rating = np.mean(neighbor_ratings)
            else:
                # If the filtered neighborhood is empty, assign the mean rating of all movies rated by the user
                predicted_rating = user_ratings[user_ratings != 0].mean()
            
            # Assign the predicted rating to the corresponding cell in the DataFrame
            predicted_ratings_train_val.at[user_id, movie_id] = predicted_rating

# Fill NaN values with mean ratings across all users
predicted_ratings_train_val.fillna(predicted_ratings_train_val.mean().mean(), inplace=True)


C:\Users\Jaume\AppData\Local\Temp\ipykernel_1720\1278750568.py:35: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  predicted_ratings_train_val.fillna(predicted_ratings_train_val.mean().mean(), inplace=True)


In [ ]:
predicted_ratings_train_val.head()

predicted_ratings_train_val.shape

movieId     30        33        44        45        50        52        66     \
userId                                                                          
377907   3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483   
211439   3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483   
2133     3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483   
2307715  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483   
2394024  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483   

movieId     68        71        77     ...     13576     13581     13594  \
userId                                 ...                                 
377907   3.624483  3.624483  3.624483  ...  3.624483  3.624483  3.624483   
211439   3.624483  3.624483  3.624483  ...  3.624483  3.624483  3.624483   
2133     3.624483  3.624483  3.624483  ...  3.624483  3.624483  3.624483   
2307715  3.624483  3.624483  3.624483  ...  3.624483  3.624483  3.624483   
2394024  3.624483  3.624483  3.624483  ...  3.624483  3.624483  3.624483   

movieId     13596     13625     13626     13629     13656     13668     13673  
userId                                                                         
377907   3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  
211439   3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  
2133     3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  
2307715  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  
2394024  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  

[5 rows x 143 columns]

(28072, 143)

Now we evaluate the model with the train-val item-user matrix.

In [ ]:
import numpy as np
from sklearn.metrics import mean_absolute_error, mean_squared_error

# Calculate item-item similarity matrix for train data
item_similarity_matrix_train = np.zeros((train.shape[1], train.shape[1]))

for i in range(train.shape[1]):
    for j in range(i, train.shape[1]):
        item_similarity_matrix_train[i, j] = cosine_similarity(train[:, i], train[:, j])
        item_similarity_matrix_train[j, i] = item_similarity_matrix_train[i, j]

# Assuming train_val_matrix and predicted_ratings_train_val are properly defined

# Now, you can evaluate the model using the evaluate_model function
mae, rmse = evaluate_model(train_val_matrix.to_numpy(), predicted_ratings_train_val)

print("Mean Absolute Error (MAE) on Train-Validation Data:", mae)
print("Root Mean Squared Error (RMSE) on Train-Validation Data:", rmse)


C:\Users\Jaume\AppData\Local\Temp\ipykernel_1720\3392059385.py:6: RuntimeWarning: invalid value encountered in scalar divide
  similarity = dot_product / (norm_a * norm_b)


Mean Absolute Error (MAE) on Train-Validation Data: 0.8980746932553374
Root Mean Squared Error (RMSE) on Train-Validation Data: 1.0738891454233717


### Step 7: Deployment

Once we have come up with the best parameters possible and trained the model with the whole train_validation set, we will test it on the test set.

In [ ]:
test_matrix

movieId  30     33     44     45     50     52     66     68     71     77     \
userId                                                                          
566255     0.0    0.0    0.0    0.0    0.0    3.0    0.0    0.0    0.0    0.0   
1877347    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2117868    5.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
150473     0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
7316       0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
...        ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2389235    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1458408    3.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1444271    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1560530    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1030342    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

movieId  ...  13576  13581  13594  13596  13625  13626  13629  13656  13668  \
userId   ...                                                                  
566255   ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1877347  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2117868  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
150473   ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
7316     ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2389235  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1458408  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1444271  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1560530  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1030342  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

movieId  13673  
userId          
566255     0.0  
1877347    0.0  
2117868    0.0  
150473     0.0  
7316       0.0  
...        ...  
2389235    0.0  
1458408    0.0  
1444271    0.0  
1560530    0.0  
1030342    0.0  

[7019 rows x 143 columns]

In [ ]:
# Check if there are NaN values in the test matrix
test_matrix.isnull().sum().sum()

0

In [ ]:
# Now, we can evaluate the model's predicted ratings on the test set

# Initialize an empty DataFrame to store predicted ratings
predicted_ratings_test = pd.DataFrame(index=test_matrix.index, columns=test_matrix.columns)

# Iterate over each user-item pair in the training set
for user_id, user_ratings in test_matrix.iterrows():
    for movie_id, rating in user_ratings.items():
        
        # Skip if the rating is non-zero (indicating a rating given by the user)
        if rating != 0:
            continue
        
        # Check if the movie has a neighborhood defined
        if movie_id in item_neighborhoods:
            neighborhood = item_neighborhoods[movie_id]
            
            # Filter out movies from the neighborhood that the user has rated in the training set
            filtered_neighborhood = [neighbor_movie_id for neighbor_movie_id in neighborhood if neighbor_movie_id in user_ratings.index and user_ratings.loc[neighbor_movie_id] != 0]
            
            # Check if there are valid indices in the filtered neighborhood
            if len(filtered_neighborhood) > 0:
                # Calculate the predicted rating for the target movie based on the neighborhood
                neighbor_ratings = [user_ratings.loc[neighbor_movie_id] for neighbor_movie_id in filtered_neighborhood]
                
                # Calculate the mean rating using only the movies in the neighborhood that have been rated by the user
                predicted_rating = np.mean(neighbor_ratings)
            else:
                # If the filtered neighborhood is empty, assign the mean rating of all movies rated by the user
                predicted_rating = user_ratings[user_ratings != 0].mean()
            
            # Assign the predicted rating to the corresponding cell in the DataFrame
            predicted_ratings_test.at[user_id, movie_id] = predicted_rating

# Fill NaN values with mean ratings across all users
predicted_ratings_test.fillna(predicted_ratings_test.mean().mean(), inplace=True)

# Now, you can evaluate the model's predicted ratings on the test set
mae, rmse = evaluate_model(test_matrix.to_numpy(), predicted_ratings_test.to_numpy())

print("Mean Absolute Error (MAE) on Test Data using Predicted Ratings from Test Set:", mae)
print("Root Mean Squared Error (RMSE) on Test Data using Predicted Ratings from Test Set:", rmse)


Mean Absolute Error (MAE) on Test Data using Predicted Ratings from Test Set: 0.8921150045546306
Root Mean Squared Error (RMSE) on Test Data using Predicted Ratings from Test Set: 1.0690393584973512


C:\Users\Jaume\AppData\Local\Temp\ipykernel_1720\1811231246.py:36: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  predicted_ratings_test.fillna(predicted_ratings_test.mean().mean(), inplace=True)


In [ ]:
top_recommendations_test = []

# Iterate over each row (user) in the test_matrix
for user_id in test_matrix.index:
    # Get the actual user ID corresponding to the user index
    recommendations = get_top_recommendations(user_id, predicted_ratings_test, df)
    top_recommendations_test.append(recommendations)

# Output: List of top movie recommendations for each user in the test matrix
top_recommendations_test

# print size of top_recommendations
print("Size of top_recommendations_test:", len(top_recommendations_test))



[['Mars Needs Women',
  'Bikini Bandits: Briefs, Shorts & Panties',
  "Something's Gotta Give",
  'Benedict Arnold: A Question of Honor',
  'Striptease'],
 ['Legend of Crystania: The Chaos Ring',
  "Something's Gotta Give",
  'Benedict Arnold: A Question of Honor',
  'Striptease',
  'Kazaam'],
 ['Legend of Crystania: The Chaos Ring',
  'Bikini Bandits: Briefs, Shorts & Panties',
  'Benedict Arnold: A Question of Honor',
  'Striptease',
  'The Deer Hunter'],
 ['Legend of Crystania: The Chaos Ring',
  'W.C. Fields',
  'Benedict Arnold: A Question of Honor',
  'Striptease',
  'The Deer Hunter'],
 ['Legend of Crystania: The Chaos Ring',
  "Something's Gotta Give",
  'Benedict Arnold: A Question of Honor',
  'Striptease',
  'Kazaam'],
 ['Legend of Crystania: The Chaos Ring',
  "Something's Gotta Give",
  'Benedict Arnold: A Question of Honor',
  'Striptease',
  'Kazaam'],
 ['NASCAR: Winston Cup 2003 Year in Review',
  'Legend of Crystania: The Chaos Ring',
  'Bikini Bandits: Briefs, Shorts 

Size of top_recommendations_test: 7019


# Item-based Classification (ItemKNN)

### Step 1: Data preparation
- Ensure you have a dataset with user-item interactions. Each interaction should include the user ID, item ID, and the corresponding label or class for classification.
- Preprocess the data as needed, including handling missing values, encoding categorical variables, and splitting into training and testing sets.

For this step we are going to resuse the `item_user_matrix` that we created in the first model built. 

### Step 2: Compute Item Similarity


In [ ]:
item_similarity_matrix_train.shape

(143, 143)

In [ ]:
import numpy as np

def item_neighborhood_selection(similarity_matrix, k=None, threshold=None, item_ids=None):
    """
    Select a subset of similar items for each item based on similarity matrix.

    Parameters:
        similarity_matrix (numpy.ndarray): Item-item similarity matrix.
        k (int): Number of similar items to select (optional).
        threshold (float): Similarity threshold for selecting similar items (optional).
        item_ids (list): List of item IDs corresponding to rows/columns of the similarity matrix.

    Returns:
        dict: Dictionary containing similar items for each item.
    """
    num_items = similarity_matrix.shape[0]
    item_neighborhood = {}

    for i in range(num_items):
        if k is not None:
            # Select top-k similar items (excluding the item itself)
            similar_items_indices = np.argsort(similarity_matrix[i])[::-1][:k]
        elif threshold is not None:
            # Select items with similarity above threshold (excluding the item itself)
            similar_items_indices = np.where(similarity_matrix[i] > threshold)[0]

        # Remove the item itself from the neighborhood
        similar_items_indices = similar_items_indices[similar_items_indices != i]

        # Get the item ID corresponding to the current index
        current_item_id = item_ids[i] if item_ids is not None else i

        # Get the item IDs for the neighborhood
        neighborhood_item_ids = [item_ids[index] for index in similar_items_indices]

        # Store the similar items with the item's ID as the key
        item_neighborhood[current_item_id] = neighborhood_item_ids

    return item_neighborhood

# Example usage:
# Assuming you have an item-item similarity matrix 'item_similarity_matrix_train'
# and you want to select top-5 similar items for each item
k = 5
item_neighborhood_classification = item_neighborhood_selection(item_similarity_matrix_train, k=k, item_ids=index_to_movie_id)

# Check if there are any items with empty neighborhoods
empty_neighborhoods = []

for item_id, neighborhood in item_neighborhood_classification.items():
    if not neighborhood:
        empty_neighborhoods.append(item_id)

if empty_neighborhoods:
    print("Items with empty neighborhoods:", empty_neighborhoods)
else:
    print("No items with empty neighborhoods found.")


No items with empty neighborhoods found.


In [ ]:
len(item_neighborhood_classification)

143

### Step 3: Ratings classification selection

In [ ]:
import numpy as np
import pandas as pd

def recommend_movies(train_matrix, item_neighborhoods, movie_id_to_index, num_movies=5):
    """
    Recommend top movies for each user based on item neighborhood.

    Parameters:
        train_matrix (np.ndarray or pd.DataFrame): Matrix containing user-item ratings in the train set.
        item_neighborhoods (dict): Dictionary containing similar items for each item.
        movie_id_to_index (dict): Dictionary mapping movie IDs to their corresponding indices in the train_matrix.
        num_movies (int): Number of movies to recommend for each user.

    Returns:
        pd.DataFrame: DataFrame containing predicted ratings for recommended movies for each user.
    """
    # Convert train_matrix to DataFrame if it's a numpy array
    if isinstance(train_matrix, np.ndarray):
        train_matrix = pd.DataFrame(train_matrix, index=np.arange(train_matrix.shape[0]), columns=np.arange(train_matrix.shape[1]))

    # Initialize an empty DataFrame to store predicted ratings
    predicted_ratings = pd.DataFrame(index=train_matrix.index, columns=train_matrix.columns)

    # Iterate over each user-item pair in the training set
    for user_id, user_ratings in train_matrix.iterrows():
        for movie_id, rating in user_ratings.items():
            
            # Skip if the rating is non-zero (indicating a rating given by the user)
            if rating != 0:
                continue
            
            # Check if the movie has a neighborhood defined
            if movie_id in item_neighborhoods:
                neighborhood = item_neighborhoods[movie_id]
                
                # Initialize a flag to track if the rating has been predicted
                rating_predicted = False
                
                # Iterate over the items in the neighborhood
                for neighbor_movie_id in neighborhood:
                    # Check if the neighbor movie has been rated by the user
                    if neighbor_movie_id in user_ratings.index and user_ratings.loc[neighbor_movie_id] != 0:
                        # Use the rating of the closest item in the neighborhood
                        predicted_rating = user_ratings.loc[neighbor_movie_id]
                        rating_predicted = True
                        break
                
                # If none of the items in the neighborhood have been rated, use the user's average rating
                if not rating_predicted:
                    if user_ratings[user_ratings != 0].empty:
                        # If the user hasn't rated any movies, use the global mean rating
                        predicted_rating = train_matrix[train_matrix != 0].mean().mean()
                    else:
                        # Use the average of the ratings given by the user
                        predicted_rating = user_ratings[user_ratings != 0].mean()
                
                # Assign the predicted rating to the corresponding cell in the DataFrame
                predicted_ratings.at[user_id, movie_id] = predicted_rating

    # Fill NaN values with mean ratings across all users
    predicted_ratings.fillna(predicted_ratings.mean().mean(), inplace=True)

    # Set the index of the DataFrame as the user ID of the train set
    predicted_ratings.index = train_matrix.index

    # Display the head of the predicted_ratings DataFrame
    print(predicted_ratings.head())

    return predicted_ratings

# Example usage:
# Assuming you have the train matrix, item neighborhood dictionary, and movie_id_to_index dictionary
# train_matrix, item_neighborhoods, movie_id_to_index = ...

# Recommend movies for each user in the train set
predicted_ratings_classification = recommend_movies(train_matrix, item_neighborhoods, movie_id_to_index)

# Print the shape of the predicted ratings matrix
print("Shape of predicted ratings matrix:", predicted_ratings_classification.shape)


movieId     30        33        44        45        50        52        66     \
userId                                                                          
704856   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
910768   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
1463003  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
147790   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
42104    3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   

movieId     68        71        77     ...     13576     13581     13594  \
userId                                 ...                                 
704856   3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
910768   3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
1463003  3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
147790   3.624147  3.624147  3.624147  ...  3.624147

C:\Users\Jaume\AppData\Local\Temp\ipykernel_1720\491492635.py:61: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  predicted_ratings.fillna(predicted_ratings.mean().mean(), inplace=True)


In [ ]:
type(train_matrix)

pandas.core.frame.DataFrame

In [ ]:
predicted_ratings_classification

movieId     30        33        44        45        50        52        66     \
userId                                                                          
704856   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
910768   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
1463003  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
147790   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
42104    3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
...           ...       ...       ...       ...       ...       ...       ...   
932047   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
594177   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
67050    3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
658375   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   
895395   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147   

movieId     68        71        77     ...     13576     13581     13594  \
userId                                 ...                                 
704856   3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
910768   3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
1463003  3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
147790   3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
42104    3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
...           ...       ...       ...  ...       ...       ...       ...   
932047   3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
594177   3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
67050    3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
658375   3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   
895395   3.624147  3.624147  3.624147  ...  3.624147  3.624147  3.624147   

movieId     13596     13625     13626     13629     13656     13668     13673  
userId                                                                         
704856   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  
910768   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  
1463003  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  
147790   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  
42104    3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  
...           ...       ...       ...       ...       ...       ...       ...  
932047   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  
594177   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  
67050    3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  
658375   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  
895395   3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  3.624147  

[22457 rows x 143 columns]

### Step 4: Recommendations Generation

In [ ]:
import pandas as pd

# Convert predicted_ratings_classification to a pandas DataFrame if it's a numpy array
if isinstance(predicted_ratings_classification, np.ndarray):
    # Use the length of train_matrix as the number of rows and items as columns
    num_users, num_items = train_matrix.shape
    predicted_ratings_classification = pd.DataFrame(predicted_ratings_classification, index=range(num_users), columns=range(num_items))

# Initialize a dictionary to store top recommendations for each user
top_recommendations_per_user = {}

# Iterate over each user in the train matrix
for user_id in train_matrix.index:
    # Get the top recommendations for the current user using predicted_ratings_classification
    recommendations = get_top_recommendations(user_id, predicted_ratings_classification, df)
    
    # Store the recommendations in the dictionary
    top_recommendations_per_user[user_id] = recommendations

# Print the top 5 recommendations for each user
for user_id, recommendations in top_recommendations_per_user.items():
    print(f"User {user_id} recommendations:", recommendations)


User 704856 recommendations: ['Mars Needs Women', 'Bikini Bandits: Briefs, Shorts & Panties', "Something's Gotta Give", 'Benedict Arnold: A Question of Honor', 'Striptease']
User 910768 recommendations: ['Aqua Teen Hunger Force: Vol. 1', 'Mars Needs Women', 'Bikini Bandits: Briefs, Shorts & Panties', 'Benedict Arnold: A Question of Honor', 'Striptease']
User 1463003 recommendations: ['Legend of Crystania: The Chaos Ring', 'Bikini Bandits: Briefs, Shorts & Panties', 'Benedict Arnold: A Question of Honor', 'Striptease', 'The Deer Hunter']
User 147790 recommendations: ['Mars Needs Women', 'Bikini Bandits: Briefs, Shorts & Panties', "Something's Gotta Give", 'Benedict Arnold: A Question of Honor', 'Striptease']
User 42104 recommendations: ['Mars Needs Women', 'Bikini Bandits: Briefs, Shorts & Panties', "Something's Gotta Give", 'Benedict Arnold: A Question of Honor', 'Striptease']
User 1082036 recommendations: ['Legend of Crystania: The Chaos Ring', 'Bikini Bandits: Briefs, Shorts & Pantie

### Step 5: Model Evaluation (Item KNN Classification)

In [ ]:
import numpy as np
import pandas as pd

# Assuming predicted_ratings_classification is your predicted ratings DataFrame or numpy array

# Ensure predicted_ratings_classification is a numpy array
if isinstance(predicted_ratings_classification, pd.DataFrame):
    predicted_ratings_classification = predicted_ratings_classification.to_numpy()

# Assuming train_matrix is the numpy array representing the item-user matrix

# Ensure train_matrix is a 2D array
if isinstance(train_matrix, pd.DataFrame):
    train_matrix = train_matrix.to_numpy()

if train_matrix.ndim == 1:
    train_matrix = np.expand_dims(train_matrix, axis=0)

# Evaluate the model
mae, rmse = evaluate_model(train, predicted_ratings_classification)

print("Mean Absolute Error (MAE) on Training Data:", mae)
print("Root Mean Squared Error (RMSE) on Training Data:", rmse)


Mean Absolute Error (MAE) on Training Data: 0.8992261735409154
Root Mean Squared Error (RMSE) on Training Data: 1.0742777997785176


### Step 6: Parameter Tuning

Experiment with different parameters such as similarity threshold, neighborhood size, and similarity metric to optimize the performance of your ItemKNN algorithm.
Use techniques like cross-validation to tune these parameters and avoid overfitting.

In [ ]:
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import NearestNeighbors
from sklearn.metrics import make_scorer
import numpy as np

# Define a custom scorer based on cosine similarity defined above
cosine_similarity_scorer = make_scorer(cosine_similarity)

# Define the parameter grid
param_grid = {
    'n_neighbors': [5, 10, 15, 30, 40],
    'metric': ['cosine', 'euclidean']
}

# Initialize NearestNeighbors model
knn_model = NearestNeighbors()

# Create the GridSearchCV object
grid_search = GridSearchCV(knn_model, param_grid, cv=5, scoring=cosine_similarity_scorer)

# Fit the data to perform hyperparameter tuning
grid_search.fit(train_val_matrix)  # train_val_matrix contains item-user matrix

# Get the best hyperparameters
best_params = grid_search.best_params_

print("Best parameters:", best_params)


c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py:993: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py", line 980, in _score
    scores = scorer(estimator, X_test, **score_params)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
TypeError: _BaseScorer.__call__() missing 1 required positional argument: 'y_true'

  warnings.warn(
c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py:993: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\Jaume\anaconda3\envs\SDM\Lib\site-packages\sklearn\model_selection\_validation.py", line 980, in _score
    scores = scorer(estimator, X_test, **score_

GridSearchCV(cv=5, estimator=NearestNeighbors(),
             param_grid={'metric': ['cosine', 'euclidean'],
                         'n_neighbors': [5, 10, 15, 30, 40]},
             scoring=make_scorer(cosine_similarity, response_method='predict'))

Best parameters: {'metric': 'cosine', 'n_neighbors': 5}


We are now going to obtain again the ratings for the full train-val set. 

In [ ]:
# Assuming you have the best model after hyperparameter tuning
# best_model = ...

# Function to recalculate predictions for a given matrix using the trained model
def recalculate_predictions(matrix):
    """
    Recalculate predictions for a given matrix using the trained model.

    Parameters:
        matrix (pd.DataFrame): Matrix containing user-item ratings.

    Returns:
        pd.DataFrame: DataFrame containing recalculated predicted ratings for each user.
    """
    # Initialize an empty DataFrame to store recalculated predicted ratings
    recalculated_predictions = pd.DataFrame(index=matrix.index, columns=matrix.columns)

    # Iterate over each user-item pair in the matrix
    for user_id, user_ratings in matrix.iterrows():
        for movie_id, rating in user_ratings.items():
            # Skip if the rating is non-zero (indicating a rating given by the user)
            if rating != 0:
                continue

            # Check if the movie has a neighborhood defined
            if movie_id in item_neighborhoods:
                neighborhood = item_neighborhoods[movie_id]

                # Initialize a flag to track if the rating has been predicted
                rating_predicted = False

                # Iterate over the items in the neighborhood
                for neighbor_movie_id in neighborhood:
                    # Check if the neighbor movie has been rated by the user
                    if neighbor_movie_id in user_ratings.index and user_ratings.loc[neighbor_movie_id] != 0:
                        # Use the rating of the closest item in the neighborhood
                        predicted_rating = user_ratings.loc[neighbor_movie_id]
                        rating_predicted = True
                        break

                # If none of the items in the neighborhood have been rated, use the user's average rating
                if not rating_predicted:
                    if user_ratings[user_ratings != 0].empty:
                        # If the user hasn't rated any movies, use the global mean rating
                        predicted_rating = matrix[matrix != 0].mean().mean()
                    else:
                        # Use the average of the ratings given by the user
                        predicted_rating = user_ratings[user_ratings != 0].mean()

                # Assign the predicted rating to the corresponding cell in the DataFrame
                recalculated_predictions.at[user_id, movie_id] = predicted_rating

    # Fill NaN values with mean ratings across all users
    recalculated_predictions.fillna(recalculated_predictions.mean().mean(), inplace=True)

    return recalculated_predictions


# Recalculate predictions for the validation set (train_val_matrix)
recalculated_val_predictions = recalculate_predictions(train_val_matrix)


C:\Users\Jaume\AppData\Local\Temp\ipykernel_1720\2334136508.py:54: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  recalculated_predictions.fillna(recalculated_predictions.mean().mean(), inplace=True)


In [ ]:
recalculated_val_predictions

movieId     30        33        44        45        50        52        66     \
userId                                                                          
377907   3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483   
211439   3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483   
2133     3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483   
2307715  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483   
2394024  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483   
...           ...       ...       ...       ...       ...       ...       ...   
1269306  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483   
478484   3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483   
860599   3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483   
63666    3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483   
1191735  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483   

movieId     68        71        77     ...     13576     13581     13594  \
userId                                 ...                                 
377907   3.624483  3.624483  3.624483  ...  3.624483  3.624483  3.624483   
211439   3.624483  3.624483  3.624483  ...  3.624483  3.624483  3.624483   
2133     3.624483  3.624483  3.624483  ...  3.624483  3.624483  3.624483   
2307715  3.624483  3.624483  3.624483  ...  3.624483  3.624483  3.624483   
2394024  3.624483  3.624483  3.624483  ...  3.624483  3.624483  3.624483   
...           ...       ...       ...  ...       ...       ...       ...   
1269306  3.624483  3.624483  3.624483  ...  3.624483  3.624483  3.624483   
478484   3.624483  3.624483  3.624483  ...  3.624483  3.624483  3.624483   
860599   3.624483  3.624483  3.624483  ...  3.624483  3.624483  3.624483   
63666    3.624483  3.624483  3.624483  ...  3.624483  3.624483  3.624483   
1191735  3.624483  3.624483  3.624483  ...  3.624483  3.624483  3.624483   

movieId     13596     13625     13626     13629     13656     13668     13673  
userId                                                                         
377907   3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  
211439   3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  
2133     3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  
2307715  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  
2394024  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  
...           ...       ...       ...       ...       ...       ...       ...  
1269306  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  
478484   3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  
860599   3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  
63666    3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  
1191735  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  3.624483  

[28072 rows x 143 columns]

In [ ]:
# Evaluate the model
mae, rmse = evaluate_model(train_val, recalculated_val_predictions)

print("Mean Absolute Error (MAE) on Train-Validation Data:", mae)
print("Root Mean Squared Error (RMSE) on Train-Validation Data:", rmse)

Mean Absolute Error (MAE) on Train-Validation Data: 0.8980746932553374
Root Mean Squared Error (RMSE) on Train-Validation Data: 1.0738891454233717


### Step 7: Deployment

Once we have all the metrics, we have to recalculate the ratings for the test set, we are going to repeat the same process for the test set.

In [ ]:
# Recalculate predictions for the validation set (test matrix)
recalculated_test_predictions = recalculate_predictions(test_matrix)

C:\Users\Jaume\AppData\Local\Temp\ipykernel_1720\2334136508.py:54: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  recalculated_predictions.fillna(recalculated_predictions.mean().mean(), inplace=True)


We also have to evaluate the metrics for the test set.

In [ ]:
# Evaluate the model
mae, rmse = evaluate_model(test, recalculated_test_predictions)

print("Mean Absolute Error (MAE) on Train-Validation Data:", mae)
print("Root Mean Squared Error (RMSE) on Train-Validation Data:", rmse)

Mean Absolute Error (MAE) on Train-Validation Data: 0.8921150045546306
Root Mean Squared Error (RMSE) on Train-Validation Data: 1.0690393584973512


In [ ]:
# Evaluate the model
mae, rmse = evaluate_model(test, recalculated_test_predictions)

print("Mean Absolute Error (MAE) on Train-Validation Data:", mae)
print("Root Mean Squared Error (RMSE) on Train-Validation Data:", rmse)

Mean Absolute Error (MAE) on Train-Validation Data: 0.8921150045546306
Root Mean Squared Error (RMSE) on Train-Validation Data: 1.0690393584973512
